##Import data & libraries

In [1]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
import random
#import missingno as msno
#from google.colab import data_table
#from tabulate import tabulate
import scipy.stats as st
import matplotlib.patches as mpl_patches
import warnings
warnings.filterwarnings("ignore")
from scipy.stats import describe
import matplotlib.cm as cm
import matplotlib.lines as mlines
from scipy.stats import pearsonr
# !pip install powerbiclient
from tqdm import tqdm

### Funciones para explorar correlaciones

In [2]:
def heatmap(df):
    plt.figure(figsize=(70,70))
    plt.rc('xtick', labelsize=40) 
    plt.rc('ytick', labelsize=40) 
    return sns.heatmap(df.corr(method='spearman'), annot=True, square=True, cmap='coolwarm', annot_kws={'size': 10})

def correlation_1_vs_all(df, feature, threshold):
    pd.set_option('display.max_rows', None)
    df = df.corr().abs().unstack().sort_values(kind="quicksort", ascending=False).reset_index()
    df.rename(columns={"level_0": "Feature 1", "level_1": "Feature 2", 0: 'Correlation Coefficient'}, inplace=True)
    df = df.drop(df[df['Correlation Coefficient'] == 1.0].index)
    return df[(df['Feature 1'] == feature) & (df['Correlation Coefficient'] > threshold)]

def correlation_all_vs_all(df, threshold, target_feature):
    pd.set_option('display.max_rows', None)
    df_temp = df.corr().abs().unstack().sort_values(kind="quicksort", ascending=False).reset_index()
    df_temp.rename(columns={"level_0": "Feature 1", "level_1": "Feature 2", 0: 'Correlation Coefficient'}, inplace=True)
    df_temp.drop(df.iloc[1::2].index, inplace=True)
    df_temp = df_temp.drop(df_temp[df_temp['Correlation Coefficient'] == 1.0].index)
    lista_feature1= df_temp['Feature 1']
    lista_feature2= df_temp['Feature 2']
    lista_corr1=[]
    lista_corr2=[]
    for x in lista_feature1:
        lista_corr1.append(np.corrcoef(df[x],df[target_feature])[0][1])
    
    for x in lista_feature2:
        lista_corr2.append(np.corrcoef(df[x],df[target_feature])[0][1])
        
    df_temp['corr1_target']= lista_corr1
    df_temp['corr2_target']= lista_corr2

    return df_temp[df_temp['Correlation Coefficient'] > threshold]

def feature_selector(df, y, threshold_y, threshold_x):

    temp_features_list = correlation_1_vs_all(df, y, threshold_y)['Feature 2'].tolist() # take main variables
    chosen_features = []

    while len(temp_features_list) > 0:

        x = temp_features_list[0]
        chosen_features.append(x)
        temp_features_list.remove(x)
        temp_correlation_list = correlation_1_vs_all(df, x, threshold_x)['Feature 2'].tolist() # take main variables

        for x in temp_correlation_list:
            if x in temp_features_list:
                temp_features_list.remove(x)

    return chosen_features



In [3]:
final_df = pd.read_csv('data/multi_df.csv')

#final_df.to_csv('data/final_df.csv')
final_df.drop(['Unnamed: 0'],axis=1,inplace=True)

final_df

Date  opening_price  highest_price  lowest_price  closing_price  \
0     2013-01-01           13.5           13.6          13.2           13.3   
1     2013-01-02           13.3           13.4          13.2           13.3   
2     2013-01-03           13.3           13.5          13.3           13.4   
3     2013-01-04           13.4           13.5          13.3           13.5   
4     2013-01-05           13.5           13.6          13.3           13.4   
...          ...            ...            ...           ...            ...   
3371  2022-03-26        44331.0        44818.0       44090.0        44548.0   
3372  2022-03-27        44542.0        46947.0       44445.0        46859.0   
3373  2022-03-28        46859.0        48199.0       46672.0        47105.0   
3374  2022-03-29        47126.0        48127.0       47029.0        47449.0   
3375  2022-03-30        47449.0        47714.0       46601.0        47075.0   

      transactions_in_blockchain  avg_block_size  sent_by_adress  \
0                        31734.0         89033.0         26174.0   
1                        39280.0        114077.0         31809.0   
2                        42147.0        108023.0         38197.0   
3                        48436.0        141811.0         34990.0   
4                        39455.0        118240.0         38008.0   
...                          ...             ...             ...   
3371                    230870.0        499029.0        440067.0   
3372                    218071.0        595651.0        421737.0   
3373                    293145.0        683575.0        520476.0   
3374                    286789.0        656320.0        519299.0   
3375                    272729.0        727827.0        485753.0   

      avg_mining_difficulty  avg_hashrate  ...  Bull_Bear_Diff macd  \
0              2.979637e+06  2.433154e+13  ...                  NaN   
1              2.979637e+06  2.280465e+13  ...                  NaN   
2              2.979637e+06  2.372489e+13  ...                  NaN   
3              2.979637e+06  2.260818e+13  ...                  NaN   
4              2.979637e+06  2.259070e+13  ...                  NaN   
...                     ...           ...  ...                  ...   
3371           2.745271e+13  2.203984e+20  ...          3733.611393   
3372           2.745271e+13  1.994591e+20  ...          2939.158344   
3373           2.745271e+13  1.925705e+20  ...          2251.462897   
3374           2.745271e+13  2.206193e+20  ...          1754.374408   
3375           2.745271e+13  1.975128e+20  ...          1313.155513   

      Social_Volume hist macd  Social_Volume signal macd  Social_Volume macd  \
0                         NaN                        NaN                 NaN   
1                         NaN                        NaN                 NaN   
2                         NaN                        NaN                 NaN   
3                         NaN                        NaN                 NaN   
4                         NaN                        NaN                 NaN   
...                       ...                        ...                 ...   
3371               -10.029531                -452.606655         -462.636186   
3372                46.186596                -441.060006         -394.873410   
3373               200.956700                -390.820831         -189.864131   
3374               178.864524                -346.104700         -167.240176   
3375               181.451843                -300.741739         -119.289896   

      Social_Volume_AI hist macd  Social_Volume_AI signal macd  \
0                            NaN                           NaN   
1                            NaN                           NaN   
2                            NaN                           NaN   
3                            NaN                           NaN   
4                            NaN                           NaN   
...                          ...    

In [4]:
#final_df.drop(['Unnamed: 0.1'],axis=1,inplace=True)


In [13]:
columnas=list(final_df.columns[1:61])

In [14]:
columnas

['opening_price',
 'highest_price',
 'lowest_price',
 'closing_price',
 'transactions_in_blockchain',
 'avg_block_size',
 'sent_by_adress',
 'avg_mining_difficulty',
 'avg_hashrate',
 'mining_profitability',
 'sent_coins_in_usd',
 'avg_transaction_fees',
 'median_transaction_fees',
 'avg_block_time',
 'avg_transaction_value',
 'median_transaction_value',
 'tweets_day',
 'google_trends',
 'active_addresses',
 'top100_to_total_percentage',
 'avg_fee_to_reward',
 'avg_price_usd',
 'market_cap_usd',
 'sf_ratio',
 'number_of_coins_in_circulation',
 'miner_revenue',
 'lbma_gold',
 'VIX_spot',
 'ETH_spot',
 'MSCIACW_spot',
 'WTI_spot',
 'FUTMSCIACWI_spot',
 'FUTBTC_spot',
 'FUTWTI',
 'FUT500',
 'FUTGOLD',
 'FUTVIX',
 'FUTDXY',
 'SP500_spot',
 'DXY_spot',
 'BDM_spot',
 'ST_UTXOs',
 'tx_volume_USD_adj',
 'Number of Transactions',
 'large_tx_volume_USD_adj',
 'large_holders_netflow',
 'in_out_ratio_adj',
 'profit_losses_ratio_adj',
 'new_addresses',
 'active_adresses',
 'Bull_Bear_Diff',
 'next_

In [15]:
for x in tqdm(columnas):
    if x!='next_day_closing_price':
        globals()[str(x)+"_df"] = final_df[[x,'next_day_closing_price']]
        final_df.drop([x],inplace=True,axis=1)
        for y in final_df.columns:
            if x.split(" ")[0] == y.split(" ")[0]:
                globals()[str(x)+"_df"][y] = final_df[y]
                final_df.drop([y],inplace=True,axis=1)

100%|██████████████████████████████████████████████████████████████████████████████████| 60/60 [01:43<00:00,  1.73s/it]


In [16]:
# Cogemos las 2 principlaes variables que no esten correlacionadas entre ellas en mas de 0.9

for x in tqdm(columnas):
    if x!='next_day_closing_price':

        for y in feature_selector(globals()[(str(x)+"_df")], 'next_day_closing_price', 0,0.9)[0:2]:
            final_df[y] =  globals()[(str(x)+"_df")][y]


100%|██████████████████████████████████████████████████████████████████████████████████| 60/60 [01:23<00:00,  1.38s/it]


In [21]:
correlation_all_vs_all(closing_price_df, 0, 'next_day_closing_price')

Feature 1                    Feature 2  \
94            closing_price dema3          closing_price tema5   
96            closing_price tema7          closing_price dema5   
98            closing_price sma 5           closing_price wma7   
100           closing_price tema3          closing_price dema3   
102                 closing_price          closing_price tema3   
104           closing_price wma10          closing_price sma 7   
106            closing_price ema5           closing_price wma7   
108            closing_price wma3           closing_price ema3   
110           closing_price dema7         closing_price tema10   
112            closing_price ema7          closing_price wma10   
114          closing_price tema15         closing_price dema10   
116           closing_price wma15         closing_price sma 10   
118            closing_price wma3          closing_price dema5   
120           closing_price tema5          closing_price tema7   
122            closing_price wma5          closing_price sma 3   
124           closing_price tema3          closing_price tema5   
126           closing_price sma 3           closing_price wma3   
128            closing_price wma5           closing_price ema3   
130            closing_price ema3          closing_price sma 3   
132            closing_price ema5           closing_price wma5   
134           closing_price dema7          closing_price dema5   
136          closing_price tema10          closing_price dema5   
138           closing_price ema10          closing_price wma15   
140           closing_price tema5          closing_price dema5   
142           closing_price dema3          closing_price tema7   
144           closing_price dema3                closing_price   
146           closing_price dema5          closing_price dema3   
148           closing_price sma 5           closing_price ema5   
150           closing_price tema7           closing_price wma3   
152            closing_price wma5           closing_price wma7   
154            closing_price ema3          closing_price dema7   
156            closing_price ema5           closing_price ema7   
158            closing_price ema3          closing_price dema5   
160            closing_price wma3          closing_price dema7   
162           closing_price tema7         closing_price tema10   
164           closing_price sma 3          closing_price dema7   
166            closing_price ema7           closing_price wma7   
168            closing_price wma3          closing_price dema3   
170           closing_price dema7         closing_price dema10   
172           closing_price tema5           closing_price wma3   
174           closing_price dema7           closing_price wma5   
176           closing_price sma 7           closing_price ema7   
178           closing_price sma 5           closing_price wma5   
180          closing_price dema10           closing_price wma5   
182           closing_price tema5                closing_price   
184            closing_price wma5           closing_price wma3   
186           closing_price dema7          closing_price tema7   
188           closing_price sma 3          closing_price dema5   
190            closing_price ema5           closing_price ema3   
192           closing_price dema7         closing_price tema15   
194            closing_price wma7          closing_price wma10   
196            closing_price ema7          closing_price ema10   
198          closing_price tema10           closing_price wma3   
200           closing_price sma 5           closing_price ema7   
202           closing_price wma10          closing_price ema10   
204           closing_price ema10         closing_price sma 10   
206          closing_price tema10          closing_price sma 3   
208           closing_price tema7           closing_price ema3   
210            closing_price wma7         closing_price dema10   
212            closing_price ema3         closing_price tema10  

In [23]:
correlation_1_vs_all(closing_price_df, 'next_day_closing_price', 0)

Feature 1                    Feature 2  \
727   next_day_closing_price                closing_price   
738   next_day_closing_price          closing_price tema3   
763   next_day_closing_price          closing_price dema3   
780   next_day_closing_price          closing_price tema5   
831   next_day_closing_price          closing_price tema7   
836   next_day_closing_price          closing_price dema5   
849   next_day_closing_price           closing_price wma3   
878   next_day_closing_price           closing_price ema3   
941   next_day_closing_price          closing_price dema7   
952   next_day_closing_price         closing_price tema10   
974   next_day_closing_price          closing_price sma 3   
1005  next_day_closing_price           closing_price wma5   
1080  next_day_closing_price         closing_price dema10   
1085  next_day_closing_price           closing_price ema5   
1128  next_day_closing_price         closing_price tema15   
1178  next_day_closing_price           closing_price wma7   
1179  next_day_closing_price   closing_price bband_upper3   
1209  next_day_closing_price          closing_price sma 5   
1220  next_day_closing_price   closing_price bband_lower3   
1247  next_day_closing_price           closing_price ema7   
1270  next_day_closing_price         closing_price dema15   
1339  next_day_closing_price          closing_price wma10   
1391  next_day_closing_price   closing_price bband_upper5   
1408  next_day_closing_price          closing_price sma 7   
1425  next_day_closing_price   closing_price bband_lower5   
1466  next_day_closing_price          closing_price ema10   
1480  next_day_closing_price         closing_price tema30   
1586  next_day_closing_price   closing_price bband_upper7   
1596  next_day_closing_price          closing_price wma15   
1622  next_day_closing_price         closing_price sma 10   
1627  next_day_closing_price   closing_price bband_lower7   
1676  next_day_closing_price         closing_price dema30   
1726  next_day_closing_price          closing_price ema15   
1793  next_day_closing_price  closing_price bband_upper10   
1900  next_day_closing_price  closing_price bband_lower10   
1921  next_day_closing_price         closing_price sma 15   
1965  next_day_closing_price         closing_price tema60   
2005  next_day_closing_price  closing_price bband_upper15   
2048  next_day_closing_price          closing_price wma30   
2237  next_day_closing_price          closing_price ema30   
2256  next_day_closing_price         closing_price dema60   
2289  next_day_closing_price  closing_price bband_lower15   
2352  next_day_closing_price         closing_price tema90   
2414  next_day_closing_price         closing_price sma 30   
2420  next_day_closing_price  closing_price bband_upper30   
2567  next_day_closing_price          closing_price wma60   
2573  next_day_closing_price         closing_price dema90   
2735  next_day_closing_price          closing_price ema60   
2880  next_day_closing_price  closing_price bband_lower30   
2952  next_day_closing_price  closing_price bband_upper60   
2957  next_day_closing_price          closing_price wma90   
3011  next_day_closing_price         closing_price sma 60   
3056  next_day_closing_price          closing_price ema90   
3147  next_day_closing_price  closing_price bband_upper90   
3240  next_day_closing_price         closing_price sma 90   
3317  next_day_closing_price  closing_price bband_lower60   
3431  next_day_closing_price        closing_price stdev90   
3545  next_day_closing_price  closing_price bband_lower90   
3651  next_day_closing_price        closing_price stdev60   
3742  next_day_closing_price        closing_price stdev15   
3904  next_day_closing_price        closing_price stdev30   
3951  next_day_closing_price        closing_price stdev10   
4037  next_day_closing_price         closing_price stdev7   
4242  next_day_closing_price         closing_price stdev5   
4269  next_day_closing_price          closing_price va

In [17]:
final_df

Date  next_day_closing_price  opening_price  \
0     2013-01-01                    13.3           13.5   
1     2013-01-02                    13.4           13.3   
2     2013-01-03                    13.5           13.3   
3     2013-01-04                    13.4           13.4   
4     2013-01-05                    13.4           13.5   
5     2013-01-06                    13.6           13.4   
6     2013-01-07                    13.7           13.4   
7     2013-01-08                    13.8           13.6   
8     2013-01-09                    14.1           13.7   
9     2013-01-10                    14.1           13.8   
10    2013-01-11                    14.2           14.1   
11    2013-01-12                    14.1           14.1   
12    2013-01-13                    14.3           14.2   
13    2013-01-14                    14.3           14.1   
14    2013-01-15                    14.7           14.3   
15    2013-01-16                    15.5           14.3   
16    2013-01-17                    15.7           14.7   
17    2013-01-18                    15.6           15.5   
18    2013-01-19                    15.7           15.7   
19    2013-01-20                    16.8           15.6   
20    2013-01-21                    17.3           15.7   
21    2013-01-22                    17.5           16.8   
22    2013-01-23                    16.9           17.3   
23    2013-01-24                    17.4           17.5   
24    2013-01-25                    17.9           16.9   
25    2013-01-26                    17.8           17.4   
26    2013-01-27                    18.7           17.9   
27    2013-01-28                    19.5           17.8   
28    2013-01-29                    19.7           18.7   
29    2013-01-30                    20.4           19.5   
30    2013-01-31                    20.5           19.7   
31    2013-02-01                    19.6           20.4   
32    2013-02-02                    20.6           20.5   
33    2013-02-03                    20.4           19.6   
34    2013-02-04                    20.6           20.6   
35    2013-02-05                    21.2           20.4   
36    2013-02-06                    22.1           20.6   
37    2013-02-07                    22.7           21.2   
38    2013-02-08                    23.6           22.1   
39    2013-02-09                    24.0           22.7   
40    2013-02-10                    24.6           23.6   
41    2013-02-11                    25.2           24.0   
42    2013-02-12                    24.2           24.6   
43    2013-02-13                    27.2           25.2   
44    2013-02-14                    27.1           24.2   
45    2013-02-15                    27.2           27.2   
46    2013-02-16                    26.8           27.1   
47    2013-02-17                    27.0           27.2   
48    2013-02-18                    29.4           26.8   
49    2013-02-19                    29.6           27.0   
50    2013-02-20                    29.8           29.4   
51    2013-02-21                    30.3           29.6   
52    2013-02-22                    29.8           29.8   
53    2013-02-23                    29.9           30.3   
54    2013-02-24                    30.4           29.8   
55    2013-02-25                    31.1           29.9   
56    2013-02-26                    30.9           30.4   
57    2013-02-27                    33.4           31.1   
58    2013-02-28                    34.5           30.9   
59    2013-03-01                    34.3           33.4   
60    2013-03-02                    34.5           34.5   
61    2013-03-03                    36.2           34.3   
62    2013-03-04                    40.3           34.5   
63    2013-03-05                    41.0           36.2   
64    2013-03-06                    42.0           40.3   
65    2013-03-07                    44.2           41.0   
66    2013-03-08                    46.8           42.0   


In [18]:
final_df.to_csv('data/2_de_cada.csv')

In [ ]:
## Para futuro mirar correlaciones negativas DXY